# Animations

We don't live in a static universe and most of the things we study in astronomy evolve in time. How do we show that in a Jupyter notebook?

The basic approaches are:

- [create a movie](#movie)
- [hack the JavaScript](#js)
- [use WebGL](#webgl)

These will be discussed in some more detail below. However, these are technologies that can interfere with one another, so most of the example code is pushed out to separate notebooks.

At the risk of getting off-topic: the notebook context is always going to impose some constraints. Getting the full power of OpenGL might mean moving [outside the browser](#opengl).

## Warning

This notebook contains some cells that deliberately use infinite loops to allow an extended simulation. 

Using Cell > Run All is ___not___ recommended here.

Be ready to use Kernel > Interrupt to stop an animation.

<a id='movie'></a>  

## Create a movie

___Matplotlib___ can do this. The basic steps are:
- create a plot with empty lists for the x and y coordinates of things you want to animate
- create an `init()` function to return an empty object and an `animate(i)` function to update the coordinates for step `i`
- call `animation.FuncAnimation()`, passing in the plot figure, the functions, and any other parameters
- use the animation object from the previous step to generate a movie in the desired format

The final section of the NewtonianOrbit notebook contains a relatively complex animation with 4 linked plots. The example below is a simplified version to illustrate the principle, with much of the code pushed to an external file to avoid clutter.

In [16]:
%matplotlib notebook

import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from IPython.display import HTML

from astropy import units as u

from scipy.integrate import solve_ivp

Generate some data for plotting. Just a simple Keplerian orbit in this case.

In [17]:
from orbits import calcOrbit

Mstar = 1*u.M_sun
a = 1*u.AU
e = 0.6 # highly elliptical - more visual

orbit_data = calcOrbit(Mstar, a, e, dt=1*u.day)
# For performance, only plot a subset of the timepoints
reduced_orbit_data = orbit_data[::3]

Define the plot but don't display it yet: use `ioff()`. The import variables are `fig_anim` referring to the figure and `planet` for the moving object.

In [18]:
plt.ioff()

# Keep a reference to the figure, we'll need it later
fig_anim = plt.figure()

plt.plot(0,0,'yo',markersize=30) # the star
plt.plot(orbit_data['x'], orbit_data['y'], lw=2)
plt.xlabel('x (AU)')
plt.ylabel('y (AU)')

# keep a reference to the object being animated
planet, = plt.plot([], [], 'go', ms=15)

plt.tight_layout() # looks nicer

`init()` is required but doesn't do much. `animate(i)` updates each frame.

In [19]:
def init():
    planet.set_data([], [])
    return planet

def animate(i):
    # called for each frame
    # this is a really bad place to put anything compute-intensive
    x = reduced_orbit_data['x'][i]
    y = reduced_orbit_data['y'][i]
    planet.set_data(x, y)
    return planet

Generate the animation object, passing in the figure, init() and animate(). 

The other parameters may need some trial and error: see https://matplotlib.org/api/_as_gen/matplotlib.animation.FuncAnimation.html

In [20]:
NFrames = reduced_orbit_data['x'].size
anim = animation.FuncAnimation(fig_anim, animate, init_func=init,
                               frames=NFrames, interval=50)

`anim` has two methods to generate a viewable representation. First `to_jshtml()`, which also gives control buttons:

In [21]:
%time HTML(anim.to_jshtml())

CPU times: user 3.99 s, sys: 42.9 ms, total: 4.03 s
Wall time: 4.03 s


The other option is `to_html5_video()`, with a different interface (mouse over the graph to see options). No speed controls, but the video will run full-screen or in a child window, and is downloadable.

In [22]:
%time HTML(anim.to_html5_video())

CPU times: user 2.35 s, sys: 77.7 ms, total: 2.43 s
Wall time: 2.56 s


### Limitations of Matplotlib animation

Mainly that everything needs to be calculated up front and you end up looping around a relatively small number of frames. 

<a id='js'></a>  

## Hack the JavaScript

___Bokeh___ is one of the newer plotting packages designed from scratch for a browser environment, so running JavaScript under a Python interface.

In [59]:
import numpy as np
import time

import bokeh
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource
from bokeh.io import push_notebook

Bokeh generally needs its data source to be a list, even if there is only one point. Define a utility function to return 1-element lists for x and y:

In [60]:
get_point = lambda i : ([orbit_data['x'][i].value, ], [orbit_data['y'][i].value, ])
num_points = orbit_data['x'].size

Bokeh in Jupyter always needs to be initialized with `output_notebook()`. 

Create a figure, then add elements to it:

In [61]:
output_notebook()
p = figure(title="Keplerian Orbit", match_aspect=True,
           x_axis_label='x (AU)', y_axis_label='y (AU)')
orbit = p.line(x=orbit_data['x'], y=orbit_data['y'], color='blue')
sun = p.circle(0, 0, color='yellow', size=30)

# Start the planet at pericenter:
px, py = get_point(0)
planet = p.circle(px, py, color='green', size=10)

Loading BokehJS ...

Define a function to move the planet to the next timestep:

In [62]:
def next_pt(i):
    i = i % num_points
    px, py = get_point(i)
    new_pt = {'x' : px, 'y' : py}

    planet.data_source.data = new_pt
    push_notebook(handle=h);

The animation will run for ever. Unfortunately the only way to stop it is with Kernel>Interrupt:

In [63]:
h = show(p, notebook_handle=True)
i = 0
try:
    while True:
        i += 1
        next_pt(i)
        time.sleep(0.01) # seconds step time
except KeyboardInterrupt:
    pass # just suppress traceback        

So far, so boring: this does about the same as Matplotlib but with a clunkier interface. At least I found syntax that works (this took several attempts, and much of what's on the web is obsolete because of API changes).

More usefully, the `next_pt()` function could do some real calculations instead of just a lookup on a pre-existing table. Some N-body code useful for this purpose is in the Bodies class (I wrote this, so treat it as demo code rather than something for serious calculations).

In [64]:
import sys
from bodies import Bodies

After creating a new Bodies instance we can add a sun and a bunch of planets. Masses, semi-major axes and ellipticities are random. All have zero inclination: we can't display $z$-values here, so it makes sense to keep the demo coplanar.

Finally we zero the center-of-mass velocity so that the simulation doesn't wander off-screen.

In [78]:
b2 = Bodies()
b2.add_sun(1*u.Msun)

nPlanets = 10
masses = np.random.rand(nPlanets)*20*u.M_earth
smas = np.random.rand(nPlanets)*10*u.AU
e = np.random.rand(nPlanets)*0.9
phis = np.random.rand(nPlanets)*359
for i in range(nPlanets):
    b2.add_planet_at_pericenter(smas[i], e[i], m=masses[i], phi=phis[i])
b2.fix_CoM() # stop the sun drifting!

The `step_Nbody()` method integrates over the period given and returns new coordinates as an $N \times 3$ array.

By default the axes auto-scale at each step. This looks terrible so we fix the ranges manually.

The `circle()` method accepts a list of colors to use. This works nicely for static plots but not with the animation (which froze, reasons currently not understood).

In [79]:
get_points = lambda : b2.step_Nbody(5*u.day).to(u.AU)
get_time = lambda : b2.get_time().to(u.year)

output_notebook()
p2 = figure(title="N-body Orbits", match_aspect=True,
           x_axis_label='x (AU)', y_axis_label='y (AU)', 
           x_range=(-10, 10), y_range=(-10, 10))

# Start the planet at pericenter:
pts = get_points()
planets = p2.circle(pts[:,0], pts[:,1], size=5, color='gray') # color=['yellow', 'green', 'blue', 'red'])

Loading BokehJS ...

Update all the coordinates at once, as well as the title:

In [80]:
def next_pt2():
#     i = i % num_points
    pts = get_points()
    t = b2.get_time()
    new_pts = {'x' : pts[:,0], 'y' : pts[:,1]} #, 'color' : ['yellow', 'green', 'blue', 'red']}
    p2.title.text = f"Time: {t:.1f}"
    planets.data_source.data = new_pts
    push_notebook(handle=h2);

Run the animation (use Kernel>interrupt to stop it).

Note that the orbits are not explicitly Keplerian: the calculation includes gravitational attraction between all pairs of bodies. Collision detection is not currently enabled (TODO).

In [1]:
h2 = show(p2, notebook_handle=True)
try:
    while True:
        next_pt2()
        time.sleep(0.02) # seconds step time
except KeyboardInterrupt:
    pass # just stop and suppress traceback        

NameError: name 'show' is not defined

### Provisional summary of Bokeh animation

It's possible, it's sometimes useful, but animation is not what Bokeh is optimized for.

Documentation in this area is pretty bad so it took some trial and error to get this far. It may be just my ignorance, but things feel a bit brittle (hence the identical gray dots).

<a id='webgl'></a>  

## Use WebGL

What? Web Graphics Library is a JavaScript API for rendering 2D and 3D graphics in a web browser. It is based on OpenGL ES.

Bottom line: it uses the graphics card to get hardware acceleration, and the results can be dramatic. It also introduces more things that can go badly wrong, so on a bad day you may need to restart the kernel pretty regularly.

Programming WebGL directly needs a detailed knowledge of both JavaScript and GLSL ES (shader language). The package `three.js` gives a higher-level interface, but it's still JS and not Python. The `pythreejs` package aims to be a bridge between this and Jupyter widgets (https://github.com/jupyter-widgets/pythreejs).

Fortunately there are several projects that try to tame WebGL (directly or via three.js) within a Python API. It's early days, though, and when the developers describe several of these projects as immature they aren't just being modest.

Given the complexity and sometimes the instability of these packages, it seems unrealistic to try running them in the same notebook. Some summary information is given below and sample code is relegated to other notebooks.

### VPython

This looks promising: a package which was written by a professor of physics for use in teaching and has been through many years of development. Plus, he provides fairly thorough documentation and lots of example code.

First problem: the long and tangled history makes searching for documentation surprisingly confusing. First the package was called `visual`, it ran outside the browser and became quite popular. Then it was renamed VPython, with similar API. Most recently, it was extensively rewritten to be browser-only using WebGL, with significant API changes ___but the same name___. What we need for Jupyter is VPython 7. Google searches throw up a lot of hits for what is now "classic VPython" (v6 or earlier), which can be actively misleading.

See https://vpython.org/contents/announcements/evolution.html for the official history, including the GlowScript online environment.

VPython is a self-contained package that tries to control all aspects of its own environment. It has its own Jupyter kernel: using the Python3 kernel won't give an error message, but behavior is unpredictable. It relies heavily on its own vector type, which is wilfully (and annoyingly) incompatible with Python standards such as NumPy and pandas. 

Overall, this can be a good way to set up small demos for teaching. It certainly does not set out to be a well-behaved component in a larger software ecosystem.

### VisPy

*Repeating the comments in `plotting/1_Plotting_intro.ipynb`:*

Focused on dynamic display of very large datasets and closely integrated with OpenGL for speed: "designed to be fast, scalable, and easy to use". http://vispy.org/

VisPy certainly isn't a drop-in replacement for Matplotlib. The installation intructions are clear up front that it "requires at least one toolkit for opening a window and creates an OpenGL context. This can be done using one of Qt, GLFW, SDL2, Wx, or Pyglet. You can also use a Jupyter notebook (version 3+) with WebGL for some visualizations although ___it is not fully functional at this time___" (my emphasis).

My experience: VisPy was easy to install on some computers, painful on others. Qt5 as a backend reliably caused segfaults, Qt4 sometimes confuses conda, wxpython is a decent fallback. The demos in GitHub are impressive (try galaxy.py), but run them from the command line. At this early stage the package is only for people comfortable with OpenGL.

___Glumpy___ is the sister project of VisPy. It is lower-level and definitely incompatible with Jupyter notebooks. 

### IPyVolume

"IPyvolume is a Python library to visualize 3d volumes and glyphs (e.g. 3d scatter plots), in the Jupyter notebook, with minimal configuration and effort. ___It is currently pre-1.0, so use at own risk.___ IPyvolume’s volshow is to 3d arrays what matplotlib’s imshow is to 2d arrays." 

That's a quote from the documentation (my emphasis added): https://ipyvolume.readthedocs.io/en/latest/. The results can be spectacular when Maarten Breddels demonstrates the package (e.g. https://www.youtube.com/watch?v=bP-JBbjwLM8). I haven't done so well with it up to now but it's something to watch: clever technology, under active development, and written by a former astronomer.

### Rebound

This is something different: "REBOUND is an N-body integrator, i.e. a software package that can integrate the motion of particles under the influence of gravity". Displaying hardware-accelerated graphics seems to be just a useful add-on.

Python user guide: https://rebound.readthedocs.io/en/latest/python_quickstart.html. Code including examples: https://github.com/hannorein/rebound

There are several examples in IPython but more in C. Translating these for Jupyter might be useful when I get the chance.

<a id='opengl'></a>  

## Move outside the browser

Clearly there are various ways to have WebGL-accelerated graphics within a Jupyter notebook. Also, projects such as IPyVolume are extending the bounds of what can be done with Python on top of JavaScript on top of GL on top of the browser. At some point, though, it may be simpler to let the program take direct control of a graphics window.

Some possibilities (mostly things I haven't tried yet):
- PyOpenGL: http://pyopengl.sourceforge.net/
- GlumPy: https://glumpy.github.io/

In the Qt framework:
- PyQt: https://github.com/baoboa/pyqt5/tree/master/examples/opengl